# Quickstart Demo

This showcases the basic operation of Local Neural Descriptor Fields (LNDF)
for a handle grasping task.  

This demonstration loads a set of grasp demos involving some randomly selected
mugs.  We can then use LNDFs to find the handles of other mugs in unique poses
or to grasp handles placed on arbitrary objects.  

If on VScode and the plots don't show, make sure to install the jupyter-notebook-renderers extension.

In [1]:
# Set the absolute base directory path here.
# This is the directory containing lndf_env.sh
lndf_base_dir = '/fastlocal/scratch/elchun/ndf_robot'
# lndf_base_dir = '/MY/LNDF/BASE/DIR'

import os
import os.path as osp

assert osp.exists(lndf_base_dir), 'Please define lndf_base_dir'

os.environ['NDF_SOURCE_DIR'] = osp.join(lndf_base_dir, 'src/ndf_robot')
os.environ['PB_PLANNING_SOURCE_DIR'] = osp.join(lndf_base_dir, 'pybullet-planning')

%env CUDA_DEVICE_ORDER=PCI_BUS_ID
%env CUDA_VISIBLE_DEVICES=7

env: CUDA_DEVICE_ORDER=PCI_BUS_ID
env: CUDA_VISIBLE_DEVICES=7


In [2]:
import random
import time

import os.path as osp

from IPython.display import clear_output

import numpy as np
import torch
from torch.nn import functional as F
import trimesh
from trimesh import viewer

from plotly.offline import init_notebook_mode, iplot
import plotly.graph_objects as go

from scipy.spatial.transform import Rotation as R
import plotly.express as px

from ndf_robot.utils import path_util, util, torch_util
from ndf_robot.utils.plotly_save import multiplot

import ndf_robot.model.vnn_occupancy_net.vnn_occupancy_net_pointnet_dgcnn \
    as vnn_occupancy_network
import ndf_robot.model.conv_occupancy_net.conv_occupancy_net \
    as conv_occupancy_network

from ndf_robot.opt.optimizer_lite import OccNetOptimizer

from ndf_robot.eval.query_points import QueryPoints

from ndf_robot.eval.demo_io import DemoIO

seed = 0
init_notebook_mode()
np.random.seed(seed)
random.seed(seed)

## Set up objects 

We insert an object, convert it to pointcloud, then set it into an upright pose.

We next find a random pose and apply that to the object.

The chart below shows both the upright and rotated object

In [22]:
def make_cut(obj_pcd, r=0.1, sample_pt=None):
    """
    Cut out portion of object that is some distance away from a sample point.

    Args:
        obj_pcd (np.ndarray): (n x 3) array representing a point cloud
        r (float): Radius of cut out.
        sample_pt (np.ndarray, optional): (1 x 3) sample point to cut around. 
            Defaults to None.
    """
    if sample_pt is None:
        sample_pt = obj_pcd[np.random.randint(0, obj_pcd.shape[0])][:]
    print(sample_pt)

    new_pcd = []
    for pt_idx in range(obj_pcd.shape[0]):
        pt = obj_pcd[pt_idx:pt_idx + 1][0]
        dis = (sum((pt.squeeze() - sample_pt)**2))**0.5
        if dis > r:
            new_pcd.append(pt)
    return np.vstack(new_pcd)



In [21]:
use_random_rotation = True
cut_pcd = True

# -- Some objects to try -- #
# obj_model = osp.join(path_util.get_ndf_obj_descriptions(), 'mug_std_centered_obj_normalized/e94e46bc5833f2f5e57b873e4f3ef3a4/models/model_normalized.obj')
# obj_model = osp.join(path_util.get_ndf_obj_descriptions(), 'bowl_handle_std_centered_obj_normalized/34875f8448f98813a2c59a4d90e63212-h/models/model_normalized.obj')
obj_model = osp.join(path_util.get_ndf_obj_descriptions(), 'bottle_handle_std_centered_obj_normalized/f853ac62bc288e48e56a63d21fb60ae9-h/models/model_normalized.obj')

obj_scale = 1.0
n_samples = 1000
assert osp.exists(obj_model), 'Object model not found'

obj_mesh = trimesh.load(obj_model, process=False)
obj_mesh.apply_scale(obj_scale)
obj_pcd = obj_mesh.sample(n_samples)

if cut_pcd:
    obj_pcd = make_cut(obj_pcd)

upright_rotation = np.eye(4)
upright_rotation[:3, :3] = util.make_rotation_matrix('x', np.pi/2)
obj_pcd = util.transform_pcd(obj_pcd, upright_rotation) 

random_rotation = np.eye(4)
if use_random_rotation:
    random_rotation[:3, :3] = R.random().as_matrix()
rotated_obj_pcd = util.transform_pcd(obj_pcd, random_rotation)

fig = multiplot([obj_pcd, rotated_obj_pcd + np.array([[0.2, 0, 0]])], write_html=False) 
fig.update_layout(coloraxis=dict(cmax=2, cmin=-1))
iplot(fig)

[ 0.02208238 -0.08682868 -0.04064026]
(474, 3)


# Create Query Points

We feed these query points into the convolutional occupancy network to 
extract our latent activations.

In [5]:
# Choose query points from these types.
QueryPointTypes = {
    'SPHERE',
    'RECT',
    'CYLINDER',
    'ARM',
    'SHELF',
    'NDF_GRIPPER',
    'NDF_RACK',
    'NDF_SHELF',
}

query_pts_type = 'RECT'
query_pts_args = {
    'n_pts': 1000,
    'x': 0.08,
    'y': 0.04,
    'z1': 0.05,
    'z2': 0.02,
}


def create_query_pts(query_pts_type, query_pts_args) -> np.ndarray:
    """
    Create query points from given config

    Args:
        query_pts_config(dict): Configs loaded from yaml file.

    Returns:
        np.ndarray: Query point as ndarray
    """

    assert query_pts_type in QueryPointTypes, 'Invalid query point type'

    if query_pts_type == 'SPHERE':
        query_pts = QueryPoints.generate_sphere(**query_pts_args)
    elif query_pts_type == 'RECT':
        query_pts = QueryPoints.generate_rect(**query_pts_args)
    elif query_pts_type == 'CYLINDER':
        query_pts = QueryPoints.generate_cylinder(**query_pts_args)
    elif query_pts_type == 'ARM':
        query_pts = QueryPoints.generate_rack_arm(**query_pts_args)
    elif query_pts_type == 'SHELF':
        query_pts = QueryPoints.generate_shelf(**query_pts_args)
    elif query_pts_type == 'NDF_GRIPPER':
        query_pts = QueryPoints.generate_ndf_gripper(**query_pts_args)
    elif query_pts_type == 'NDF_RACK':
        query_pts = QueryPoints.generate_ndf_rack(**query_pts_args)
    elif query_pts_type == 'NDF_SHELF':
        query_pts = QueryPoints.generate_ndf_shelf(**query_pts_args)

    return query_pts

query_pts = create_query_pts(query_pts_type, query_pts_args)


fig = multiplot([query_pts, obj_pcd + np.array([[0.2, 0, 0]]), rotated_obj_pcd + np.array([[0.4, 0, 0]])], 
                write_html=False) 
fig.update_layout(coloraxis=dict(cmax=3, cmin=-1))
iplot(fig)

## Create Model 

Define LNDF Model

In [6]:
model_args = {
    'latent_dim': 128,  # Number of voxels in convolutional occupancy network
    'model_type': 'pointnet',  # Encoder type
    'return_features': True,  # Return latent features for evaluation
    'sigmoid': False,  # Use sigmoid activation on last layer
    'acts': 'last',  # Return last activations of occupancy network
}
model_checkpoint = 'ndf_vnn/conv_occ_hidden128_anyrot_multicategory_latent_sim_occ_neg_se3_s4_7/checkpoints/model_epoch_0001_iter_060000.pth' 
model_checkpoint_path = osp.join(path_util.get_ndf_model_weights(), model_checkpoint)

model = conv_occupancy_network.ConvolutionalOccupancyNetwork(**model_args)
model.load_state_dict(torch.load(model_checkpoint_path))

<All keys matched successfully>

## Create Pose Optimizer

In [7]:
optimizer_args = {
    'opt_iterations': 500,
    'rand_translate': True,
    'use_tsne': False,
    'M_override': 20,
}

opt_viz_path = 'temp'

optimizer = OccNetOptimizer(model, query_pts, viz_path=opt_viz_path,
                            **optimizer_args)

## Load Demos

In [8]:
demo_exp = 'mug/mug_handle_converted'
n_demos = 10

demo_load_dir = osp.join(path_util.get_ndf_data(), 'demos', demo_exp)
demo_fnames = os.listdir(demo_load_dir)

assert len(demo_fnames), 'No demonstrations found in path: %s!' \
    % demo_load_dir

# Sort out grasp demos
grasp_demo_fnames = [osp.join(demo_load_dir, fn) for fn in
    demo_fnames if 'grasp_demo' in fn]

demo_shapenet_ids = []
demo_list = []


# Iterate through all demos, extract relevant information and
# prepare to pass into optimizer
random.shuffle(grasp_demo_fnames)
for grasp_demo_fn in grasp_demo_fnames[:n_demos]:
    print('Loading grasp demo from fname: %s' % grasp_demo_fn)
    grasp_data = np.load(grasp_demo_fn, allow_pickle=True)

    demo = DemoIO.process_grasp_data(grasp_data)
    demo_list.append(demo)

    optimizer.add_demo(demo)
    demo_shapenet_ids.append(demo.obj_shapenet_id)

optimizer.process_demos()
clear_output(wait=True)
print('Shapenet IDs used in demo:')
for id in demo_shapenet_ids:
    print('  ' + id)



Shapenet IDs used in demo:
  73b8b6456221f4ea20d3c05c08e26f
  daee5cf285b8d210eeb8d422649e5f2b
  928a383f79698c3fb6d9bc28c8d8a2c4
  187859d3c3a2fd23f54e1b6f41fdd78a
  6c379385bf0a23ffdec712af445786fe
  586e67c53f181dc22adf8abaa25e0215
  8f550770386a6cf82f23d8349a133d2b
  61c10dccfa8e508e2d66cbf6a91063
  7a8ea24474846c5c2f23d8349a133d2b
  8f6c86feaa74698d5c91ee20ade72edc


In [9]:
sample_demo = demo_list[0]
demo_obj_pts = sample_demo.obj_pts
# demo_query_pts = sample_demo.query_pts
demo_query_pts = query_pts 
demo_obj_pose = sample_demo.obj_pose_world
demo_query_pose = sample_demo.query_pose_world

posed_obj_pts = util.apply_pose_numpy(demo_obj_pts, demo_obj_pose)
posed_query_pts = util.apply_pose_numpy(demo_query_pts, demo_query_pose)
fig = multiplot([posed_obj_pts, posed_query_pts], write_html=False)
iplot(fig)

## Get target pose

In [10]:
pose_mats, best_idx, intermediates = optimizer.optimize_transform_implicit(
    rotated_obj_pcd, ee=True, viz_path=opt_viz_path, return_intermediates=True)

[DEBUG][2023-01-31 14:09:26]: i: 99, losses: 0.086918, 0.087233, 0.074540, 0.087639, 0.081609, 0.097593, 0.068820, 0.081255, 0.089378, 0.108283, 0.088399, 0.078370, 0.090011, 0.103108, 0.107374, 0.072277, 0.105635, 0.085299, 0.071304, 0.094937
[DEBUG][2023-01-31 14:09:27]: i: 199, losses: 0.075591, 0.064755, 0.073703, 0.087005, 0.069572, 0.072412, 0.061257, 0.071314, 0.087331, 0.106271, 0.086985, 0.067732, 0.087869, 0.092215, 0.106644, 0.061445, 0.098475, 0.084682, 0.061442, 0.093638
[DEBUG][2023-01-31 14:09:28]: i: 299, losses: 0.067579, 0.061339, 0.070839, 0.086938, 0.062476, 0.071781, 0.061435, 0.067632, 0.087015, 0.101333, 0.086910, 0.067559, 0.087548, 0.091422, 0.075817, 0.061262, 0.089846, 0.084676, 0.061253, 0.092788
[DEBUG][2023-01-31 14:09:29]: i: 399, losses: 0.067530, 0.061242, 0.061266, 0.086947, 0.061295, 0.071629, 0.061307, 0.067591, 0.086920, 0.075403, 0.086917, 0.067515, 0.087561, 0.091349, 0.073332, 0.061235, 0.089690, 0.084659, 0.061337, 0.092599
[DEBUG][2023-01-31 14

In [11]:
idx = best_idx
best_pose_mat = pose_mats[idx]

final_query_pts = util.transform_pcd(query_pts, best_pose_mat)

# Generate trail of intermediate optimization results
intermediate_query_pts = []
query_pts_mean = np.mean(query_pts, axis=0).reshape(1, 3)
for iter_mats in intermediates:
    iter_query_pts = util.transform_pcd(query_pts_mean, iter_mats[idx])
    intermediate_query_pts.append(iter_query_pts)

# Plot all the results
plot_list = [
    rotated_obj_pcd,
    final_query_pts,
] + intermediate_query_pts

plot_pts = np.vstack(plot_list)

# Assign different colors to different objects
color = np.ones(plot_pts.shape[0])
color[rotated_obj_pcd.shape[0]:rotated_obj_pcd.shape[0] + final_query_pts.shape[0]] *= 2
color[rotated_obj_pcd.shape[0] + final_query_pts.shape[0]:] *= 3
fig = px.scatter_3d(
    x=plot_pts[:, 0], y=plot_pts[:, 1], z=plot_pts[:, 2], color=color)
fig.update_layout(coloraxis=dict(cmax=max(color) + 1, cmin=-1))

iplot(fig)